# The Battle of Neighborhoods

## Introduction

In the era of globalization, people moves a lot looking for better life and better work opportunities. Sometimes, this move becomes very hectic when it is to a completely unknown country or place. We people always have our own preference which might not match with other person. For example, my brother. He lives in India and works for a major US based IT firm. His company got a very good project to be executed for a client based out of Toronto, Canada. So my brother's company wants him to move to Toronto, Canada. 

This is the first time, my brother is moving outside of India and is completely confused in selecting the neighborhood for his staying. After doing almost a month's research, he reached out to me to help him out in selecting or recommending the neighborhood which will be best for him to stay.

When I started enquiring about his preferences, he came up with the following to be used as selection criteria:
 
 - Safe Neighborhood
 - Transportation - Metro Station, Bus Station
 - Breakfast places
 - Coffee Shops
 - Restaurants (Indian, Italian, Thai and American)
 - Shopping Center
 - Selected Bars - Sports Bar, Cocktail Bar, Pub
 - Outdoor Activity Center - Playground, Park
 
With these criteria provided by my brother, I would like to recommend to my brother which neighborhood of Toronto, Canada will be good for his living. The basis of this work will help the people like my brother to find their kind of neighborhood considering their preferences in mind. 



# Data Sources

### Neighborhood Data Source:
In Toronto, there are total 140 neighborhoods. To get the list of these neighborhood and their boundary information, I will be using the data from the below URL:
	http://data.torontopolice.on.ca/datasets/neighbourhood-crime-rates-boundary-file-
The data available in this page holds the below information:
	- Name of the neighborhood
	- Geometric information about the neighborhood (coordinates of the boundary)
	- Average crime rate for specific crimes till 2018.

I will use an Open Data Portal based API to access this data. The API RUL is : https://opendata.arcgis.com/datasets/af500b5abb7240399853b35a2362d0c0_0.geojson  

From this dataset, I will use only the name of neighborhood, the boundary coordinates. Crime data will be skipped due to old information (data till 2018). This dataset has the boundary coordinates of each neighborhood, which is not suitable for getting the venues. As, the boundary coordinates are nothing but the coordinates of a polygon, that is why using the boundary coordinates, I have calculated the centroids of all the neighborhood and assigned them as centroid coordinates of each neighborhood. 

### Crime Data:
Basically Toronto is one of the safest place in the world, but in recent years, crime has started rising in some of the neighborhoods. We will use the crime incident data published by Toronto Police Department. This data set captured all the major crime reports since 2014 covering for all the 140 neighborhoods. The URL is: http://data.torontopolice.on.ca/datasets/mci-2014-to-2019. 

I have used the API exposed by Open Data Portal to access this data programmatically. The service URL is: https://opendata.arcgis.com/datasets/f4c2e5de021f4836a3caf77f8421f487_0.geojson. This dataset also contains the coordinates of all the places of the incidents. These coordinate information is not relevant here, so I will ignore those information.

In this dataset, the name of the neighborhood was having some additional information (HOOD ID, some number related to Toronto police data), which I had to strip it out so that both the neighborhood dataset and crime dataset
can have same neighborhood name.

As safety is his one of the priority, rather than considering all the 140 neighborhoods, I will take first 100 lowest crime based neighborhood.

From this dataset, I will use the below information:
 - Name of the neighborhood (after removing the Hood ID from the name)
 - Crime Incident
Then I will count the number of incidents for each neighborhood.

### Foursquare Venue data:
My brother has shared his preferred venues which he wants near to his future place of residence. It is quite possible that all venues might not be available at all neighborhood. To collect the list of preferred venues, I will be using the category hierarchy list to identify the categoryId of each preferred categories to filter out the non-preferred venues. The link for the Foursquare category list is below:
	https://developer.foursquare.com/docs/build-with-foursquare/categories/
	
Going through this page, at first I will collect all the nearest and closest categoryIds for all the preferred facilities my brother is looking for. Then I will use the Foursquare API for searching the venues by passing all these categoryIds. 

From this Foursquare dataset, we will collect all the preferred venues (name of the venue and venue category name) present for each 100 neighborhoods.

We will use clustering technique to group the neighborhoods based on their availability near to each neighborhood and then come up with the recommendations. 


### Collecting and building required Datasets

Import all required Python pachages

In [1]:
import pandas as pd
import numpy as np
import json
import requests
from pandas.io.json import json_normalize
import folium
from IPython.display import HTML
from geopy.geocoders import Nominatim

In [2]:
# The code was removed by Watson Studio for sharing.

Use geolocaotor package to retrieve the coordinates of Toronro,Canada. This coordinates will be used to keep Toronto city at the center of the map.

In [4]:
city_name = "Toronto, Ontario"

geolocator = Nominatim(user_agent="toronto_explorer")
location = geolocator.geocode(city_name)
toronto_latitude = location.latitude
toronto_longitude = location.longitude
print('The geograpical coordinate of Toronto are {}, {}.'.format(toronto_latitude, toronto_longitude))

The geograpical coordinate of Toronto are 43.6534817, -79.3839347.


In [5]:
# Create an utility to determine the centroid (coordinates) of a neighborhood
# using the boundary coordinates
def getCentroidCoordinates(coordinates):
    det = 0.0
    tempDet = 0.0
    centroidX = 0.0
    centroidY = 0.0
    j = 0
    count = len(coordinates)
    for i in range(count):
        if i + 1 == count:
            j = 0
        else:
            j = i + 1
        tempDet = ((coordinates[i][1]*coordinates[j][0]) - (coordinates[j][1] * coordinates[i][0]))
        det += tempDet
        centroidX += (coordinates[i][1] + coordinates[j][1])*tempDet;
        centroidY += (coordinates[i][0] + coordinates[j][0])*tempDet;
        
    ## divide by the total mass of the polygon
    centroidX /= (3*det);
    centroidY /= (3*det);
    return centroidX, centroidY

#### Collecting the neighborhood data

I am using an Open Data Portal based API to access the neighborhood data. 

The API URL is : https://opendata.arcgis.com/datasets/af500b5abb7240399853b35a2362d0c0_0.geojson

From this datasource, I am trying to fetch the below features:
  - Name of the Neighborhood
  - Boundary coordinates of respective neighborhoods

In [6]:
toronto_neighborhood_url = 'https://opendata.arcgis.com/datasets/af500b5abb7240399853b35a2362d0c0_0.geojson'
neighborhood_results = requests.get(toronto_neighborhood_url).json()
neighborhoods = neighborhood_results["features"]

In [7]:
neighborhood_list=[]
for neighborhood in neighborhoods:
    name = neighborhood["properties"]["Neighbourhood"]
    population = neighborhood["properties"]["Population"]
    neighbor_geometry = neighborhood["geometry"]["coordinates"][0]
    # Calculate the centroid coordinates using the boundary coordinates
    latitude, longitude = getCentroidCoordinates(neighbor_geometry)
    neighborhood_list.append([name, latitude, longitude])
    


neighborhood_df = pd.DataFrame([item for item in neighborhood_list])
neighborhood_df.columns = ["Neighborhood", "Latitude", "Longitude"]
neighborhood_df.head(10)

Neighborhood   Latitude  Longitude
0                Yonge-St.Clair  43.687859 -79.397831
1       York University Heights  43.765738 -79.488842
2              Lansing-Westgate  43.754272 -79.424706
3            Yorkdale-Glen Park  43.714673 -79.457068
4           Stonegate-Queensway  43.635520 -79.501091
5        Tam O'Shanter-Sullivan  43.780130 -79.302876
6                   The Beaches  43.671049 -79.299560
7  Thistletown-Beaumond Heights  43.737989 -79.563452
8              Thorncliffe Park  43.707749 -79.349944
9            Danforth East York  43.689468 -79.331362

In [8]:
toronto_neighborhood_map = folium.Map(location=[toronto_latitude, toronto_longitude], zoom_start=10)

# add markers to map
for lat, lng, neighborhood in zip(neighborhood_df['Latitude'], neighborhood_df['Longitude'], neighborhood_df['Neighborhood']):
    label = '{}'.format(neighborhood)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(toronto_neighborhood_map)  
    
folium.LayerControl().add_to(toronto_neighborhood_map)

toronto_neighborhood_map

The Map can be viewed here as below


![Toronto_Neighborhood_Map.JPG](https://github.com/bitunsen/Coursera_Capstone/raw/master/Toronto_Neighborhood_Map.JPG)



    

#### Collecting crime data from Toronto Police department

I will be using another Open Data Portal based API to access details of the major crime incidents. 

The data can be visualized in the Toronto Police Department website: http://data.torontopolice.on.ca/datasets/mci-2014-to-2019/data

The API URL is : https://opendata.arcgis.com/datasets/f4c2e5de021f4836a3caf77f8421f487_0.geojson

From this datasource, I am trying to fetch the below features:
  - Name of the Neighborhood
  - Major Crime Incident since 2014 till 2019
  


In [10]:
toronto_crime_url = 'https://opendata.arcgis.com/datasets/f4c2e5de021f4836a3caf77f8421f487_0.geojson'
crime_results = requests.get(toronto_crime_url).json()
crime_features = crime_results["features"]

Using this major crime incident dataset, we will create a new dataframe "crime_df". I will count all the major criminal incidents and the percentage of crime per neighborhood.

Then sort of "crime_df" dataframe by "Crime_Count" column.

In [12]:
crime_list = []
for feature in crime_features:
    name = feature["properties"]["Neighbourhood"]
    clean_name = name[0:name.find("(")].strip()
    #print("Neighborhood Name : " + name)
    crime_list.append([clean_name, 1])
    

toronto_crime_df = pd.DataFrame([item for item in crime_list])
toronto_crime_df.columns = ["Neighborhood", "Crime_Count"]
toronto_crime_df = toronto_crime_df.groupby(["Neighborhood"]).count()
toronto_crime_df.sort_values(by="Crime_Count", ascending = True, inplace=True)
toronto_crime_df = toronto_crime_df.reset_index()
toronto_crime_df['Percentage_Crime']= (toronto_crime_df['Crime_Count'])/toronto_crime_df['Crime_Count'].sum()
toronto_crime_df.head(10)

Neighborhood  Crime_Count  Percentage_Crime
0  Lambton Baby Point          353          0.001710
1    Woodbine-Lumsden          377          0.001826
2          Maple Leaf          410          0.001986
3           Guildwood          411          0.001991
4      Yonge-St.Clair          412          0.001996
5       Markland Wood          413          0.002001
6       Old East York          479          0.002320
7           Casa Loma          480          0.002325
8   Forest Hill South          494          0.002393
9      Kingsway South          496          0.002403

So the safest neighborhood is Lambton Baby Point. The second safest neighborhood is Woodbine-Lumsden.

Let's see the neighborhood which are having higher criminal incidents.

In [13]:
toronto_crime_df.tail(10)

Neighborhood  Crime_Count  Percentage_Crime
130                          West Hill         3497          0.016940
131                             Woburn         3798          0.018398
132               Kensington-Chinatown         3823          0.018519
133               Downsview-Roding-CFB         3974          0.019251
134            York University Heights         3989          0.019323
135                          Moss Park         4786          0.023184
136             West Humber-Clairville         5702          0.027621
137              Church-Yonge Corridor         6232          0.030189
138                Bay Street Corridor         6817          0.033023
139  Waterfront Communities-The Island         7747          0.037528

So the highest crime rate is at Waterfront Communities-The Island. Compare to the number of incidents at Lambton Baby Point, the number of incidents at Waterfront communities is quite at higher side. 

So I would have to make sure not to recommend this neighborhood to my brother.

Let's visualize the Crime rate based division through Toronto's neighborhood map.

In [14]:
url = 'https://github.com/bitunsen/Coursera_Capstone/raw/master'
toronto_geo = f'{url}/toronto_neighborhood.geojson'
toronto_crime_map = folium.Map(location=[43.653522, -79.510540], zoom_start=10)

folium.Choropleth(
    geo_data=toronto_geo,
    name='choropleth',
    data=toronto_crime_df,
    columns=['Neighborhood', 'Percentage_Crime'],
    key_on='feature.properties.AREA_NAME',
    fill_color='YlGn',
    fill_opacity=0.7,
    line_opacity=0.2,
    legend_name='Crime Rate (%)'
).add_to(toronto_crime_map)

folium.LayerControl().add_to(toronto_crime_map)

toronto_crime_map

The Map can be viewed here as below


![Toronto_Crime_Data_Map.jpg](https://github.com/bitunsen/Coursera_Capstone/raw/master/Toronto_Crime_Data_Map.jpg)



We will join both data sources by the neighborhood name and then create a dataframe having below columns:
 - Neighborhood - Name of the neighborhood
 - Total number of Crime in a neighborhood
 - Percentage of Crime in a neighborhood
 - Centroid coordinates of each neighborhood (calculated using the boundary coordinates)



In [15]:
neighborhood_with_crime_df = pd.merge(toronto_crime_df, neighborhood_df, on="Neighborhood")
neighborhood_with_crime_df.head(10)

Neighborhood  Crime_Count  Percentage_Crime   Latitude  Longitude
0  Lambton Baby Point          353          0.001710  43.657421 -79.496008
1    Woodbine-Lumsden          377          0.001826  43.694107 -79.311123
2          Maple Leaf          410          0.001986  43.715575 -79.480718
3           Guildwood          411          0.001991  43.748827 -79.195014
4      Yonge-St.Clair          412          0.001996  43.687859 -79.397831
5       Markland Wood          413          0.002001  43.633542 -79.573394
6       Old East York          479          0.002320  43.696781 -79.335448
7           Casa Loma          480          0.002325  43.681852 -79.407967
8   Forest Hill South          494          0.002393  43.694526 -79.414278
9      Kingsway South          496          0.002403  43.653522 -79.510540

In [16]:
neighborhood_with_crime_df.shape

(140, 5)

Now we will visualize the neighborhood data using the Map.

In [28]:
url = 'https://github.com/bitunsen/Coursera_Capstone/raw/master'
toronto_geo = f'{url}/toronto_neighborhood.geojson'
neighborhood_crime_map = folium.Map(location=[43.653522, -79.510540], zoom_start=10)

folium.Choropleth(
    geo_data=toronto_geo,
    name='choropleth',
    data=neighborhood_with_crime_df,
    columns=['Neighborhood', 'Percentage_Crime'],
    key_on='feature.properties.AREA_NAME',
    fill_color='YlGn',
    fill_opacity=0.7,
    line_opacity=0.2,
    legend_name='Crime Rate (%)'
).add_to(neighborhood_crime_map)

# add markers to map
for lat, lng, neighborhood, crime_count in zip(neighborhood_with_crime_df['Latitude'], neighborhood_with_crime_df['Longitude'], neighborhood_with_crime_df['Neighborhood'], neighborhood_with_crime_df['Crime_Count']):
    label = neighborhood + ", Crime Count : [{}]".format(crime_count)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=2,
        popup=label,
        color='blue',
        fill=True,
        fill_color='blue',
        fill_opacity=0.7,
        parse_html=False).add_to(neighborhood_crime_map)
    
folium.LayerControl().add_to(neighborhood_crime_map)

neighborhood_crime_map

This map can be visualized here:

![Toronto_Neighborhood_With_Crime_Map.jpg](https://github.com/bitunsen/Coursera_Capstone/raw/master/Toronto_Neighborhood_With_Crime_Map.jpg)



My brother's one of the preference is safety. That is why rather than considering all the neighborhoods, we will take first 120 safer heighborhood for further analysis.

In [67]:
safe_neighborhood_with_crime_df = neighborhood_with_crime_df.head(120)
safe_neighborhood_with_crime_df.head(5)

Neighborhood  Crime_Count  Percentage_Crime   Latitude  Longitude
0  Lambton Baby Point          353          0.001710  43.657421 -79.496008
1    Woodbine-Lumsden          377          0.001826  43.694107 -79.311123
2          Maple Leaf          410          0.001986  43.715575 -79.480718
3           Guildwood          411          0.001991  43.748827 -79.195014
4      Yonge-St.Clair          412          0.001996  43.687859 -79.397831

In [68]:
safe_neighborhood_with_crime_df.shape

(120, 5)

#### Collect venue data for the selected 120 neighborhood

Here we will use Foursquare seach venue API to find the venues which my brother prefers. He is looking for the below venues:
 - Transportation - Metro Station, Bus Station
 - Breakfast places
 - Coffee Shops
 - Restaurants (Indian, Italian, Thai and American)
 - Shopping Center
 - Selected Bars - Sports Bar, Cocktail Bar, Pub
 - Outdoor Activity Center - Playground, Park
 


With the help of the Foursquare documentation, I hace collected all the relevant category ids which I will be using while looking for venues of those categories. The URL for this is below
  - [Foursquare Categories](https://developer.foursquare.com/docs/build-with-foursquare/categories/)
  

In [31]:
CATEGORY_ID_LIST = ["4bf58dd8d48988d1fd931735","4bf58dd8d48988d10f941735","4bf58dd8d48988d110941735","4bf58dd8d48988d149941735",
                    "4bf58dd8d48988d14e941735","4bf58dd8d48988d1fd941735","5744ccdfe4b0c0459246b4dc","4bf58dd8d48988d11d941735",
                    "4bf58dd8d48988d11e941735","4bf58dd8d48988d11b941735", "4bf58dd8d48988d1e7941735", "4bf58dd8d48988d163941735",
                    "4bf58dd8d48988d143941735", "52e81612bcbc57f1066b79f4", "4bf58dd8d48988d1e0931735", "52f2ab2ebcbc57f1066b8b4f"]

In [33]:
#CATEGORY_ID_QUERY = "4bf58dd8d48988d1fd931735,4bf58dd8d48988d10f941735,4bf58dd8d48988d110941735,4bf58dd8d48988d149941735,4bf58dd8d48988d14e941735,4bf58dd8d48988d1fd941735,5744ccdfe4b0c0459246b4dc,4bf58dd8d48988d11d941735,4bf58dd8d48988d11e941735,4bf58dd8d48988d11b941735,4bf58dd8d48988d1e7941735,4bf58dd8d48988d163941735,4bf58dd8d48988d143941735,52e81612bcbc57f1066b79f4,4bf58dd8d48988d1e0931735,52f2ab2ebcbc57f1066b8b4f,4bf58dd8d48988d1fe931735"
## Added all the categoryIds for the preferred venues as a string variable
## This variable will be used to query the venues near to each neighborhood

CATEGORY_ID_QUERY = ("4bf58dd8d48988d1fd931735,4bf58dd8d48988d10f941735,4bf58dd8d48988d110941735,4bf58dd8d48988d149941735"
                     ",4bf58dd8d48988d14e941735,4bf58dd8d48988d1fd941735,5744ccdfe4b0c0459246b4dc,4bf58dd8d48988d11d941735"
                     ",4bf58dd8d48988d11e941735,4bf58dd8d48988d11b941735,4bf58dd8d48988d1e7941735,4bf58dd8d48988d163941735"
                     ",4bf58dd8d48988d143941735,52e81612bcbc57f1066b79f4,4bf58dd8d48988d1e0931735,52f2ab2ebcbc57f1066b8b4f"
                     ",4bf58dd8d48988d1fe931735")

## This utility method will use latitude and longitude of a neighborhood and fetch the venues of these categories

def getVenuesByForNeighborhood(neighborhood_name, category_id_list, latitudes, longitudes, radius=1500):
    venues_list=[]
    venue_id_dict = dict()
    
    url = "https://api.foursquare.com/v2/venues/search?ll={},{}&radius={}&limit=60&categoryId={}&client_id={}&client_secret={}&v={}".format(
                latitudes, longitudes, radius, CATEGORY_ID_QUERY, CLIENT_ID, CLIENT_SECRET, VERSION)
        
        
    #print(url)
    #print("**************************************************************************************************************************")
    response = requests.get(url).json()["response"]
    venues = requests.get(url).json()["response"]['venues']
    if len(venues) == 0:
        print("Neighborhood [{}] has no venues listed.".format(neighborhood_name))
        
    else:
        #print("Neighborhood [{}] has {} venues listed.".format(neighborhood_name, len(venues)))
        for venue in venues:
            venue_id = venue["id"]
            venue_name = venue["name"]
            if len(venue["categories"]) == 0:
                continue
            venue_category = venue["categories"][0]["name"]
            venue_category_id = venue["categories"][0]["id"]
            if venue_category_id in category_id_list:
                #print("Venue Details :: ID : [{}] ::: Name : [{}] ::: Category : [{}]".format(venue_id, venue_name, venue_category))
                if venue_id in venue_id_dict:
                    #print("Venue Details :: ID : [{}] ::: Name : [{}] is already added. Skipping it now.".format(venue_id, venue_name))
                    continue
                else:
                    #print("Venue Details :: ID : [{}] ::: Name : [{}] is not added. Adding it now.".format(venue_id, venue_name))
                    venue_id_dict[venue_id] = venue_name
                    venues_list.append([neighborhood_name, venue_name, venue_category])
                    
    #print(venue_id_dict)
    return venues_list
    

Use the neighborhood data which was collected and consolidated from the previous data sources and then for each neighborhood collect the targeted venues.

Create a new dataframe with the below features for further venue analysis:
  - Neighborhood Name
  - Name of the Venue
  - Categoty Name of the Venue

In [34]:

consolidated_venue_list = []
for neighborhood_name, latitude, longitude in zip(safe_neighborhood_with_crime_df["Neighborhood"], safe_neighborhood_with_crime_df["Latitude"], 
                                                  safe_neighborhood_with_crime_df["Longitude"]):
    venues_list = getVenuesByForNeighborhood(neighborhood_name, CATEGORY_ID_LIST, latitude, longitude)
    print("Neighborhood {} has {} venues.".format(neighborhood_name, len(venues_list)))
    consolidated_venue_list.extend(venues_list)
    
neighborhood_venue_df = pd.DataFrame(venue for venue in consolidated_venue_list)
neighborhood_venue_df.columns = ["Neighborhood", "Venue_Name", "Category"]

neighborhood_venue_df.head(10)



Neighborhood Lambton Baby Point has 42 venues.
Neighborhood Woodbine-Lumsden has 41 venues.
Neighborhood Maple Leaf has 29 venues.
Neighborhood Guildwood has 20 venues.
Neighborhood Yonge-St.Clair has 45 venues.
Neighborhood Markland Wood has 36 venues.
Neighborhood Old East York has 43 venues.
Neighborhood Casa Loma has 42 venues.
Neighborhood Forest Hill South has 44 venues.
Neighborhood Kingsway South has 38 venues.
Neighborhood Centennial Scarborough has 23 venues.
Neighborhood Humber Heights-Westmount has 35 venues.
Neighborhood Mount Pleasant East has 44 venues.
Neighborhood Lawrence Park North has 45 venues.
Neighborhood Etobicoke West Mall has 34 venues.
Neighborhood Bayview Woods-Steeles has 21 venues.
Neighborhood Alderwood has 42 venues.
Neighborhood Bridle Path-Sunnybrook-York Mills has 18 venues.
Neighborhood Princess-Rosethorn has 23 venues.
Neighborhood Forest Hill North has 45 venues.
Neighborhood Pleasant View has 42 venues.
Neighborhood Runnymede-Bloor West Village ha

Neighborhood                 Venue_Name            Category
0  Lambton Baby Point               Magwood Park                Park
1  Lambton Baby Point        Jane Subway Station       Metro Station
2  Lambton Baby Point                       RGLR         Coffee Shop
3  Lambton Baby Point                Tim Hortons         Coffee Shop
4  Lambton Baby Point                     Strada  Italian Restaurant
5  Lambton Baby Point         La Veranda Osteria  Italian Restaurant
6  Lambton Baby Point    Old Mill Subway Station       Metro Station
7  Lambton Baby Point  Royal York Subway Station       Metro Station
8  Lambton Baby Point               Bryden's Pub                 Pub
9  Lambton Baby Point                  Starbucks         Coffee Shop

In [35]:
neighborhood_venue_df.head(10)

Neighborhood                 Venue_Name            Category
0  Lambton Baby Point               Magwood Park                Park
1  Lambton Baby Point        Jane Subway Station       Metro Station
2  Lambton Baby Point                       RGLR         Coffee Shop
3  Lambton Baby Point                Tim Hortons         Coffee Shop
4  Lambton Baby Point                     Strada  Italian Restaurant
5  Lambton Baby Point         La Veranda Osteria  Italian Restaurant
6  Lambton Baby Point    Old Mill Subway Station       Metro Station
7  Lambton Baby Point  Royal York Subway Station       Metro Station
8  Lambton Baby Point               Bryden's Pub                 Pub
9  Lambton Baby Point                  Starbucks         Coffee Shop

In [36]:
neighborhood_venue_df.shape

(4444, 3)

Lets see the counts of venues by venue category per neighborhood:

In [37]:
neighborhood_venue_df.groupby(['Neighborhood', 'Category']).count()

Venue_Name
Neighborhood                 Category                       
Agincourt North              Breakfast Spot                1
                             Bus Stop                      1
                             Coffee Shop                   8
                             Indian Restaurant             8
                             Park                          8
                             Playground                    2
                             Shopping Mall                 8
                             Shopping Plaza                2
Agincourt South-Malvern West American Restaurant           3
                             Breakfast Spot                1
                             Bus Stop                      1
                             Coffee Shop                  13
                             Indian Restaurant             4
                             Italian Restaurant            3
                             Park                          4
                             Pub                           2
                             Shopping Mall                 7
                             Thai Restaurant               1
Alderwood                    American Restaurant           1
                             Breakfast Spot                3
                             Bus Stop                      2
                             Cocktail Bar                  1
                             Coffee Shop                  15
                             Indian Restaurant             1
                             Italian Restaurant            1
                             Park                          7
                             Playground                    2
                             Pub                           2
                             Shopping Mall                 4
                             Thai Restaurant               3
...                                                      ...
Yonge-Eglinton               Italian Restaurant            7
                             Metro Station                 3
                             Park                          4
                             Playground                    1
                             Pub                           5
                             Shopping Mall                 2
                             Thai Restaurant               2
Yonge-St.Clair               American Restaurant           3
                             Breakfast Spot                1
                             Coffee Shop                  12
                             Indian Restaurant             1
                             Italian Restaurant            3
                             Metro Station                 5
                             Park                          9
                             Playground                    1
                             Pub                           7
                             Shopping Mall                 1
                             Sports Bar                    2
Yorkdale-Glen Park           American Restaurant           5
                             Bus Stop                      4
                             Coffee Shop                  11
                             Indian Restaurant             2
                             Italian Restaurant            4
                             Metro Station                 3
                             Park                          3
                             Playground                    3
                             Pub                           1
                             Shopping Mall                 4
                             Sports Bar                    1
                             Thai Restaurant               2

[1191 rows x 1 columns]

In [38]:
neighborhood_venue_df.groupby('Neighborhood').count()

Venue_Name  Category
Neighborhood                                           
Agincourt North                            38        38
Agincourt South-Malvern West               39        39
Alderwood                                  42        42
Banbury-Don Mills                          34        34
Bathurst Manor                             36        36
Bayview Village                            43        43
Bayview Woods-Steeles                      21        21
Bedford Park-Nortown                       41        41
Beechborough-Greenbrook                    42        42
Birchcliffe-Cliffside                      35        35
Black Creek                                33        33
Blake-Jones                                42        42
Briar Hill-Belgravia                       44        44
Bridle Path-Sunnybrook-York Mills          18        18
Broadview North                            39        39
Brookhaven-Amesbury                        30        30
Cabbagetown-South St.James Town            41        41
Caledonia-Fairbank                         42        42
Casa Loma                                  42        42
Centennial Scarborough                     23        23
Clanton Park                               37        37
Cliffcrest                                 22        22
Corso Italia-Davenport                     42        42
Danforth                                   41        41
Danforth East York                         42        42
Don Valley Village                         37        37
Dorset Park                                42        42
Dufferin Grove                             38        38
East End-Danforth                          38        38
Edenbridge-Humber Valley                   21        21
...                                       ...       ...
Rosedale-Moore Park                        43        43
Rouge                                       7         7
Runnymede-Bloor West Village               44        44
Rustic                                     33        33
Scarborough Village                        27        27
South Parkdale                             39        39
St.Andrew-Windfields                       48        48
Steeles                                    38        38
Stonegate-Queensway                        47        47
Tam O'Shanter-Sullivan                     43        43
Taylor-Massey                              33        33
The Beaches                                42        42
Thistletown-Beaumond Heights               35        35
Thorncliffe Park                           44        44
Trinity-Bellwoods                          37        37
University                                 44        44
Victoria Village                           43        43
Westminster-Branson                        30        30
Weston                                     36        36
Weston-Pellam Park                         43        43
Wexford/Maryvale                           40        40
Willowdale East                            45        45
Willowdale West                            38        38
Willowridge-Martingrove-Richview           32        32
Woodbine Corridor                          43        43
Woodbine-Lumsden                           41        41
Wychwood                                   42        42
Yonge-Eglinton                             42        42
Yonge-St.Clair                             45        45
Yorkdale-Glen Park                         43        43

[120 rows x 2 columns]

In [39]:
print('There are {} uniques categories.'.format(len(neighborhood_venue_df['Category'].unique())))

There are 16 uniques categories.


We are planning to do a clustering analysis, so we need to convert our category features into numerical feature. We will perform a well-known transformation called <b>"One hot encoding"</b>.

In [40]:
# one hot encoding
neighborhood_venue_one_hot_df = pd.get_dummies(neighborhood_venue_df[['Category']], prefix="", prefix_sep="")
neighborhood_venue_one_hot_df.shape

(4444, 16)

In [41]:
neighborhood_venue_one_hot_df.head(5)

American Restaurant  Breakfast Spot  Buffet  Bus Stop  Cocktail Bar  \
0                    0               0       0         0             0   
1                    0               0       0         0             0   
2                    0               0       0         0             0   
3                    0               0       0         0             0   
4                    0               0       0         0             0   

   Coffee Shop  Indian Restaurant  Italian Restaurant  Metro Station  Park  \
0            0                  0                   0              0     1   
1            0                  0                   0              1     0   
2            1                  0                   0              0     0   
3            1                  0                   0              0     0   
4            0                  0                   1              0     0   

   Playground  Pub  Shopping Mall  Shopping Plaza  Sports Bar  Thai Restaurant  
0           0    0              0               0           0                0  
1           0    0              0               0           0                0  
2           0    0              0               0           0                0  
3           0    0              0               0           0                0  
4           0    0              0               0           0                0

You might have noticed that the above dataframe doesn't have the Neighborhood feature. Let's add it from the <b>neighborhood_venue_df</b> dataframe.



In [42]:
neighborhood_venue_one_hot_df.insert(0, 'Neighborhood', neighborhood_venue_df['Neighborhood'])
neighborhood_venue_one_hot_df.head(5)

Neighborhood  American Restaurant  Breakfast Spot  Buffet  Bus Stop  \
0  Lambton Baby Point                    0               0       0         0   
1  Lambton Baby Point                    0               0       0         0   
2  Lambton Baby Point                    0               0       0         0   
3  Lambton Baby Point                    0               0       0         0   
4  Lambton Baby Point                    0               0       0         0   

   Cocktail Bar  Coffee Shop  Indian Restaurant  Italian Restaurant  \
0             0            0                  0                   0   
1             0            0                  0                   0   
2             0            1                  0                   0   
3             0            1                  0                   0   
4             0            0                  0                   1   

   Metro Station  Park  Playground  Pub  Shopping Mall  Shopping Plaza  \
0              0     1           0    0              0               0   
1              1     0           0    0              0               0   
2              0     0           0    0              0               0   
3              0     0           0    0              0               0   
4              0     0           0    0              0               0   

   Sports Bar  Thai Restaurant  
0           0                0  
1           0                0  
2           0                0  
3           0                0  
4           0                0

Now let's convert the full dataset per neighborhood for better understanding.

In [43]:
neighborhood_venue_grouped_df = neighborhood_venue_one_hot_df.groupby('Neighborhood').mean().reset_index()
neighborhood_venue_grouped_df.shape

(120, 17)

In [44]:
neighborhood_venue_grouped_df.head(5)

Neighborhood  American Restaurant  Breakfast Spot  Buffet  \
0               Agincourt North             0.000000        0.026316     0.0   
1  Agincourt South-Malvern West             0.076923        0.025641     0.0   
2                     Alderwood             0.023810        0.071429     0.0   
3             Banbury-Don Mills             0.029412        0.029412     0.0   
4                Bathurst Manor             0.083333        0.027778     0.0   

   Bus Stop  Cocktail Bar  Coffee Shop  Indian Restaurant  Italian Restaurant  \
0  0.026316       0.00000     0.210526           0.210526            0.000000   
1  0.025641       0.00000     0.333333           0.102564            0.076923   
2  0.047619       0.02381     0.357143           0.023810            0.023810   
3  0.029412       0.00000     0.264706           0.058824            0.147059   
4  0.083333       0.00000     0.305556           0.027778            0.083333   

   Metro Station      Park  Playground       Pub  Shopping Mall  \
0            0.0  0.210526    0.052632  0.000000       0.210526   
1            0.0  0.102564    0.000000  0.051282       0.179487   
2            0.0  0.166667    0.047619  0.047619       0.095238   
3            0.0  0.294118    0.000000  0.000000       0.058824   
4            0.0  0.194444    0.111111  0.000000       0.055556   

   Shopping Plaza  Sports Bar  Thai Restaurant  
0        0.052632    0.000000         0.000000  
1        0.000000    0.000000         0.025641  
2        0.000000    0.000000         0.071429  
3        0.000000    0.000000         0.088235  
4        0.000000    0.027778         0.000000

In [47]:
neighborhood_venue_grouped_df.loc[neighborhood_venue_grouped_df["Buffet"] > 0.0]

Neighborhood  American Restaurant  Breakfast Spot    Buffet  \
5        Bayview Village             0.000000        0.023256  0.023256   
37     Forest Hill South             0.000000        0.045455  0.022727   
44     Hillcrest Village             0.000000        0.054054  0.027027   
59   Lawrence Park South             0.023810        0.071429  0.023810   
68   Mount Pleasant East             0.000000        0.045455  0.022727   
69   Mount Pleasant West             0.000000        0.045455  0.022727   
97               Steeles             0.026316        0.052632  0.026316   
117       Yonge-Eglinton             0.000000        0.023810  0.023810   

     Bus Stop  Cocktail Bar  Coffee Shop  Indian Restaurant  \
5    0.023256           0.0     0.279070           0.023256   
37   0.022727           0.0     0.386364           0.000000   
44   0.054054           0.0     0.324324           0.027027   
59   0.000000           0.0     0.309524           0.047619   
68   0.000000           0.0     0.272727           0.090909   
69   0.000000           0.0     0.295455           0.068182   
97   0.026316           0.0     0.236842           0.000000   
117  0.000000           0.0     0.333333           0.047619   

     Italian Restaurant  Metro Station      Park  Playground       Pub  \
5              0.046512       0.069767  0.255814    0.069767  0.000000   
37             0.068182       0.068182  0.204545    0.045455  0.090909   
44             0.054054       0.000000  0.270270    0.000000  0.027027   
59             0.142857       0.071429  0.095238    0.047619  0.119048   
68             0.136364       0.068182  0.113636    0.022727  0.113636   
69             0.136364       0.068182  0.136364    0.022727  0.090909   
97             0.000000       0.026316  0.210526    0.131579  0.000000   
117            0.166667       0.071429  0.095238    0.023810  0.119048   

     Shopping Mall  Shopping Plaza  Sports Bar  Thai Restaurant  
5         0.046512        0.046512    0.000000         0.093023  
37        0.045455        0.000000    0.000000         0.000000  
44        0.135135        0.027027    0.000000         0.000000  
59        0.023810        0.000000    0.000000         0.023810  
68        0.022727        0.000000    0.022727         0.068182  
69        0.045455        0.000000    0.000000         0.068182  
97        0.236842        0.026316    0.000000         0.000000  
117       0.047619        0.000000    0.000000         0.047619

This dataframe <b>neighborhood_venue_grouped_df</b> we will use for the clustering the neighborhood to statistically group the neighborhoods by ther number of venues.

We will create another dataframe which will help us visualizing the neighborhoods by their popular venues.


Now lets sort the venues by occurance per neighborhood. This will give us a good perspective to understand which venue category is is having higher presence in each neighborhood.

To achieve that, lets right a small utility function which will do the sorting for us. If any neighborhood does not have any particular venue category, then it will display "NA" after the name of the vaenue category. For example "Pub NA", in case if Pub category venue is not present in any particular neighborhood.

In [48]:
def getTopVenues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    sorted_venues = []
    for category in row_categories_sorted.index:
        #print("Category {} ::: Score :: {}".format(category,row_categories_sorted[category]))
        if row_categories_sorted[category] > 0.0:
            sorted_venues.append(category)
        else:
            sorted_venues.append(category + " NA")
    #print(row_categories_sorted)
    #return row_categories_sorted.index.values[0:num_top_venues]
    return sorted_venues

In [61]:
num_top_venues = 16

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhood_venues_sorted_df = pd.DataFrame(columns=columns)
neighborhood_venues_sorted_df['Neighborhood'] = neighborhood_venue_grouped_df['Neighborhood']

for ind in np.arange(neighborhood_venue_grouped_df.shape[0]):
    neighborhood_venues_sorted_df.iloc[ind, 1:] = getTopVenues(neighborhood_venue_grouped_df.iloc[ind, :], num_top_venues)

neighborhood_venues_sorted_df.head(5)

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0               Agincourt North         Shopping Mall                  Park   
1  Agincourt South-Malvern West           Coffee Shop         Shopping Mall   
2                     Alderwood           Coffee Shop                  Park   
3             Banbury-Don Mills                  Park           Coffee Shop   
4                Bathurst Manor           Coffee Shop                  Park   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0     Indian Restaurant           Coffee Shop        Shopping Plaza   
1                  Park     Indian Restaurant    Italian Restaurant   
2         Shopping Mall       Thai Restaurant        Breakfast Spot   
3    Italian Restaurant       Thai Restaurant         Shopping Mall   
4            Playground    Italian Restaurant              Bus Stop   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0            Playground              Bus Stop        Breakfast Spot   
1   American Restaurant                   Pub       Thai Restaurant   
2                   Pub            Playground              Bus Stop   
3     Indian Restaurant              Bus Stop        Breakfast Spot   
4   American Restaurant         Shopping Mall            Sports Bar   

  9th Most Common Venue 10th Most Common Venue 11th Most Common Venue  \
0    Thai Restaurant NA          Sports Bar NA                 Pub NA   
1              Bus Stop         Breakfast Spot          Sports Bar NA   
2    Italian Restaurant      Indian Restaurant           Cocktail Bar   
3   American Restaurant          Sports Bar NA      Shopping Plaza NA   
4     Indian Restaurant         Breakfast Spot     Thai Restaurant NA   

  12th Most Common Venue 13th Most Common Venue 14th Most Common Venue  \
0       Metro Station NA  Italian Restaurant NA        Cocktail Bar NA   
1      Shopping Plaza NA          Playground NA       Metro Station NA   
2    American Restaurant          Sports Bar NA      Shopping Plaza NA   
3                 Pub NA          Playground NA       Metro Station NA   
4      Shopping Plaza NA                 Pub NA       Metro Station NA   

  15th Most Common Venue  16th Most Common Venue  
0              Buffet NA  American Restaurant NA  
1        Cocktail Bar NA               Buffet NA  
2       Metro Station NA               Buffet NA  
3        Cocktail Bar NA               Buffet NA  
4        Cocktail Bar NA               Buffet NA

Looks like Agincourt North does not have any Thai Resturant, Sport Bar, Pub etc. It only has Shopping Mall, Park, Indian Resturant, Coffe Shop, Shopping Plaza, Playground, Bus Stop and Breakfast Spot. Which means, if someone with strong preference of Thai cuisine, might go to Alderwood neighborhood, as it's 4th common venue is Thai Resturant. 

Lets see what type of venues we can get in the safest neighborhood <b>Lambton Baby Point</b>

In [62]:
neighborhood_venues_sorted_df.loc[neighborhood_venues_sorted_df["Neighborhood"] == "Lambton Baby Point"]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
56  Lambton Baby Point           Coffee Shop                  Park   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
56            Playground    Italian Restaurant         Metro Station   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
56        Breakfast Spot                   Pub              Bus Stop   

   9th Most Common Venue 10th Most Common Venue 11th Most Common Venue  \
56       Thai Restaurant      Indian Restaurant           Cocktail Bar   

   12th Most Common Venue 13th Most Common Venue 14th Most Common Venue  \
56    American Restaurant          Sports Bar NA      Shopping Plaza NA   

   15th Most Common Venue 16th Most Common Venue  
56       Shopping Mall NA              Buffet NA

Looks like <b>Lambton Baby Point</b> has almost all preferred venues other than shopping malls.

Now lets go ahead and apply clustering technique on our dataset.

Lets import the neccessary python package to do the K-mean clustering.

In [63]:
from sklearn.cluster import KMeans

In [64]:
kclusters = 3

neighborhood_venue_clustering_df = neighborhood_venue_grouped_df.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(neighborhood_venue_clustering_df)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([0, 1, 1, 0, 0, 0, 2, 1, 2, 2], dtype=int32)

In [65]:
neighborhood_venues_sorted_df.insert(1, 'Cluster Labels', kmeans.labels_)

neighborhood_venues_sorted_df.head(5)

Neighborhood  Cluster Labels 1st Most Common Venue  \
0               Agincourt North               0         Shopping Mall   
1  Agincourt South-Malvern West               1           Coffee Shop   
2                     Alderwood               1           Coffee Shop   
3             Banbury-Don Mills               0                  Park   
4                Bathurst Manor               0           Coffee Shop   

  2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0                  Park     Indian Restaurant           Coffee Shop   
1         Shopping Mall                  Park     Indian Restaurant   
2                  Park         Shopping Mall       Thai Restaurant   
3           Coffee Shop    Italian Restaurant       Thai Restaurant   
4                  Park            Playground    Italian Restaurant   

  5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0        Shopping Plaza            Playground              Bus Stop   
1    Italian Restaurant   American Restaurant                   Pub   
2        Breakfast Spot                   Pub            Playground   
3         Shopping Mall     Indian Restaurant              Bus Stop   
4              Bus Stop   American Restaurant         Shopping Mall   

  8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  \
0        Breakfast Spot    Thai Restaurant NA          Sports Bar NA   
1       Thai Restaurant              Bus Stop         Breakfast Spot   
2              Bus Stop    Italian Restaurant      Indian Restaurant   
3        Breakfast Spot   American Restaurant          Sports Bar NA   
4            Sports Bar     Indian Restaurant         Breakfast Spot   

  11th Most Common Venue 12th Most Common Venue 13th Most Common Venue  \
0                 Pub NA       Metro Station NA  Italian Restaurant NA   
1          Sports Bar NA      Shopping Plaza NA          Playground NA   
2           Cocktail Bar    American Restaurant          Sports Bar NA   
3      Shopping Plaza NA                 Pub NA          Playground NA   
4     Thai Restaurant NA      Shopping Plaza NA                 Pub NA   

  14th Most Common Venue 15th Most Common Venue  16th Most Common Venue  
0        Cocktail Bar NA              Buffet NA  American Restaurant NA  
1       Metro Station NA        Cocktail Bar NA               Buffet NA  
2      Shopping Plaza NA       Metro Station NA               Buffet NA  
3       Metro Station NA        Cocktail Bar NA               Buffet NA  
4       Metro Station NA        Cocktail Bar NA               Buffet NA

Now lets merge this venue and cluster specific information with the crime and coordinate information of each neighborhood.

We will join the below dataframes by using the "Neighborhood" feature of each dataframe
    - safe_neighborhood_with_crime_df
    - neighborhood_venues_sorted_df

In [69]:
safe_neighborhood_with_crime_df = safe_neighborhood_with_crime_df.join(neighborhood_venues_sorted_df.set_index('Neighborhood'), on='Neighborhood')
safe_neighborhood_with_crime_df.head(5)

Neighborhood  Crime_Count  Percentage_Crime   Latitude  Longitude  \
0  Lambton Baby Point          353          0.001710  43.657421 -79.496008   
1    Woodbine-Lumsden          377          0.001826  43.694107 -79.311123   
2          Maple Leaf          410          0.001986  43.715575 -79.480718   
3           Guildwood          411          0.001991  43.748827 -79.195014   
4      Yonge-St.Clair          412          0.001996  43.687859 -79.397831   

   Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
0               1           Coffee Shop                  Park   
1               0           Coffee Shop              Bus Stop   
2               0                  Park           Coffee Shop   
3               0                  Park           Coffee Shop   
4               1           Coffee Shop                  Park   

  3rd Most Common Venue 4th Most Common Venue  ... 7th Most Common Venue  \
0            Playground    Italian Restaurant  ...                   Pub   
1                  Park            Playground  ...        Breakfast Spot   
2              Bus Stop            Playground  ...       Thai Restaurant   
3            Sports Bar         Shopping Mall  ...            Playground   
4                   Pub         Metro Station  ...            Sports Bar   

  8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  \
0              Bus Stop       Thai Restaurant      Indian Restaurant   
1       Thai Restaurant    Italian Restaurant           Cocktail Bar   
2         Shopping Mall    Italian Restaurant         Breakfast Spot   
3    Thai Restaurant NA     Shopping Plaza NA       Metro Station NA   
4         Shopping Mall            Playground      Indian Restaurant   

  11th Most Common Venue 12th Most Common Venue 13th Most Common Venue  \
0           Cocktail Bar    American Restaurant          Sports Bar NA   
1          Sports Bar NA      Shopping Plaza NA       Shopping Mall NA   
2      Shopping Plaza NA                 Pub NA       Metro Station NA   
3  Italian Restaurant NA   Indian Restaurant NA        Cocktail Bar NA   
4         Breakfast Spot     Thai Restaurant NA      Shopping Plaza NA   

  14th Most Common Venue 15th Most Common Venue  16th Most Common Venue  
0      Shopping Plaza NA       Shopping Mall NA               Buffet NA  
1                 Pub NA              Buffet NA  American Restaurant NA  
2   Indian Restaurant NA        Cocktail Bar NA               Buffet NA  
3              Buffet NA      Breakfast Spot NA  American Restaurant NA  
4        Cocktail Bar NA            Bus Stop NA               Buffet NA  

[5 rows x 22 columns]

Let us see which neighrborhoods are present cluster 0 

In [70]:
safe_neighborhood_with_crime_df.loc[safe_neighborhood_with_crime_df["Cluster Labels"] == 0]

Neighborhood  Crime_Count  Percentage_Crime  \
1                    Woodbine-Lumsden          377          0.001826   
2                          Maple Leaf          410          0.001986   
3                           Guildwood          411          0.001991   
5                       Markland Wood          413          0.002001   
9                      Kingsway South          496          0.002403   
19                  Forest Hill North          565          0.002737   
20                      Pleasant View          570          0.002761   
24                   Elms-Old Rexdale          593          0.002873   
26                             Rustic          607          0.002940   
33       Thistletown-Beaumond Heights          692          0.003352   
36                        Long Branch          725          0.003512   
37                     Bathurst Manor          727          0.003522   
39     Eringate-Centennial-West Deane          787          0.003812   
40                         Henry Farm          787          0.003812   
42                            Steeles          806          0.003904   
44                  Hillcrest Village          810          0.003924   
49                            Ionview          859          0.004161   
50                  Woodbine Corridor          877          0.004248   
52                   Thorncliffe Park          903          0.004374   
54                    Bayview Village          927          0.004491   
57               Briar Hill-Belgravia          930          0.004505   
59               St.Andrew-Windfields          987          0.004781   
60                        New Toronto          996          0.004825   
67                        The Beaches         1116          0.005406   
68                       Clanton Park         1117          0.005411   
71                      Taylor-Massey         1147          0.005556   
74                    Agincourt North         1157          0.005605   
75                   Victoria Village         1158          0.005610   
76                Brookhaven-Amesbury         1162          0.005629   
77                    Flemingdon Park         1163          0.005634   
78                  Banbury-Don Mills         1205          0.005837   
79                         Cliffcrest         1217          0.005895   
80                Westminster-Branson         1218          0.005900   
82                  High Park-Swansea         1233          0.005973   
84                        Morningside         1245          0.006031   
85                Englemount-Lawrence         1248          0.006045   
86   Willowridge-Martingrove-Richview         1252          0.006065   
92                  O'Connor-Parkview         1420          0.006879   
94                 Don Valley Village         1495          0.007242   
95                         Humbermede         1521          0.007368   
96                Scarborough Village         1528          0.007402   
100                          Oakridge         1660          0.008041   
102                  Newtonbrook West         1693          0.008201   
105                 Parkwoods-Donalda         1752          0.008487   
106                          Milliken         1799          0.008715   
107                     Eglinton East         1865          0.009034   
108                        L'Amoreaux         1866          0.009039   
109                 East End-Danforth         1895          0.009180   
114                      Kennedy Park         2043          0.009897   
115                       Black Creek         2069          0.010023   
116                       Dorset Park         2109          0.010216   
118                  Wexford/Maryvale         2419          0.011718   

      Latitude  Longitude  Cluster Labels 1st Most Common Venue  \
1    43.694107 -79.311123               0           Coffee Shop   
2    43.715575 -79.480718               0                  Park   
3    43

In [71]:
safe_neighborhood_with_crime_df.loc[safe_neighborhood_with_crime_df["Cluster Labels"] == 1]

Neighborhood  Crime_Count  Percentage_Crime  \
0                 Lambton Baby Point          353          0.001710   
4                     Yonge-St.Clair          412          0.001996   
6                      Old East York          479          0.002320   
7                          Casa Loma          480          0.002325   
8                  Forest Hill South          494          0.002393   
12               Mount Pleasant East          509          0.002466   
13               Lawrence Park North          513          0.002485   
16                         Alderwood          545          0.002640   
21      Runnymede-Bloor West Village          573          0.002776   
22                Leaside-Bennington          582          0.002819   
23                   Broadview North          593          0.002873   
27               Lawrence Park South          627          0.003037   
29                Humewood-Cedarvale          645          0.003124   
30                Danforth East York          666          0.003226   
31                Caledonia-Fairbank          678          0.003284   
32                       Blake-Jones          679          0.003289   
34          Playter Estates-Danforth          707          0.003425   
35                    Highland Creek          716          0.003468   
41                          Wychwood          801          0.003880   
43                   Rexdale-Kipling          810          0.003924   
45                    Yonge-Eglinton          823          0.003987   
46                          Danforth          841          0.004074   
47                  Newtonbrook East          853          0.004132   
48                Weston-Pellam Park          858          0.004156   
51                   North Riverdale          888          0.004302   
53            Corso Italia-Davenport          918          0.004447   
56                  Lansing-Westgate          929          0.004500   
61                   Little Portugal         1015          0.004917   
62                   Willowdale West         1035          0.005014   
63                    Dufferin Grove         1049          0.005082   
64                       Regent Park         1052          0.005096   
65           Palmerston-Little Italy         1053          0.005101   
66                   High Park North         1070          0.005183   
69                     Junction Area         1119          0.005421   
70                      Roncesvalles         1138          0.005513   
72               Stonegate-Queensway         1148          0.005561   
73                 Greenwood-Coxwell         1155          0.005595   
81   Cabbagetown-South St.James Town         1223          0.005924   
83              Bedford Park-Nortown         1240          0.006007   
88                   Oakwood Village         1261          0.006108   
89               Rosedale-Moore Park         1276          0.006181   
90               Mount Pleasant West         1293          0.006263   
93                        University         1455          0.007048   
98                 Trinity-Bellwoods         1572          0.007615   
99      Agincourt South-Malvern West         1650          0.007993   
101                    Humber Summit         1670          0.008090   
103              North St.James Town         1721          0.008337   
110                  Willowdale East         1904          0.009223   
112               Yorkdale-Glen Park         1998          0.009679   
117                   South Parkdale         2121          0.010274   
119                          Niagara         2465          0.011941   

      Latitude  Longitude  Cluster Labels 1st Most Common Venue  \
0    43.657421 -79.496008               1           Coffee Shop   
4    43.687859 -79.397831               1           Coffee Shop   
6    43.696781 -79.335448               1           Coffee Shop   
7    43.681852 -79.407967               1           Coffee Shop

In [72]:
safe_neighborhood_with_crime_df.loc[safe_neighborhood_with_crime_df["Cluster Labels"] == 2]

Neighborhood  Crime_Count  Percentage_Crime  \
10              Centennial Scarborough          508          0.002461   
11            Humber Heights-Westmount          509          0.002466   
14                 Etobicoke West Mall          515          0.002495   
15               Bayview Woods-Steeles          539          0.002611   
17   Bridle Path-Sunnybrook-York Mills          560          0.002713   
18                  Princess-Rosethorn          563          0.002727   
25             Beechborough-Greenbrook          605          0.002931   
28            Edenbridge-Humber Valley          634          0.003071   
38            Keelesdale-Eglinton West          785          0.003803   
55                Pelmo Park-Humberlea          928          0.004495   
58                        Mount Dennis          953          0.004616   
87       Kingsview Village-The Westway         1255          0.006079   
91              Tam O'Shanter-Sullivan         1371          0.006641   
97                   Rockcliffe-Smythe         1558          0.007547   
104              Birchcliffe-Cliffside         1730          0.008380   
111                             Weston         1942          0.009407   
113                              Rouge         2042          0.009892   

      Latitude  Longitude  Cluster Labels 1st Most Common Venue  \
10   43.782374 -79.150802               2                  Park   
11   43.692235 -79.522378               2                  Park   
14   43.645063 -79.568901               2                  Park   
15   43.796802 -79.382076               2                  Park   
17   43.731014 -79.378865               2                  Park   
18   43.666053 -79.544522               2                  Park   
25   43.693217 -79.479433               2                  Park   
28   43.670889 -79.522420               2                  Park   
38   43.685728 -79.471399               2                  Park   
55   43.717517 -79.528244               2                  Park   
58   43.688145 -79.499951               2                  Park   
87   43.698995 -79.547824               2                  Park   
91   43.780130 -79.302876               2                  Park   
97   43.674791 -79.494382               2                  Park   
104  43.694682 -79.265049               2                  Park   
111  43.702718 -79.515684               2                  Park   
113  43.821199 -79.186310               2                  Park   

    2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  ...  \
10             Playground           Coffee Shop    Italian Restaurant  ...   
11            Coffee Shop            Playground       Thai Restaurant  ...   
14            Coffee Shop              Bus Stop         Shopping Mall  ...   
15            Coffee Shop         Shopping Mall            Playground  ...   
17            Coffee Shop              Bus Stop         Shopping Mall  ...   
18             Playground           Coffee Shop              Bus Stop  ...   
25            Coffee Shop   American Restaurant         Shopping Mall  ...   
28             Playground         Shopping Mall           Coffee Shop  ...   
38            Coffee Shop              Bus Stop         Shopping Mall  ...   
55            Coffee Shop        Breakfast Spot       Thai Restaurant  ...   
58            Coffee Shop            Playground              Bus Stop  ...   
87            Coffee Shop            Playground         Shopping Mall  ...   
91            Coffee Shop         Shopping Mall              Bus Stop  ...   
97            Coffee Shop            Playground              Bus Stop  ...   
104     Indian Restaurant              Bus Stop           Coffee Shop  ...   
111           Coffee Shop              Bus Stop       Thai Restaurant  ...   
113            Playground           Coffee Shop    Thai Restaurant NA  ...   

    7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
10          Sports Bar NA 